In [1]:
import os
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import dataclasses
import physiokit as pk
from scipy import signal

In [2]:
df = pd.read_csv("../datasets/pulse-transit-time-ppg/s3_sit.csv", parse_dates=['time'])

In [3]:
sig_fs = 500
fs = 250
dur_len = 30*sig_fs
ts = df['time'].to_numpy()[:dur_len]
ecg = df['ecg'].to_numpy()[:dur_len]
ppg1 = df['pleth_1'].to_numpy()[:dur_len]
ppg2 = df['pleth_2'].to_numpy()[:dur_len]
rr_peaks = df['peaks'].to_numpy()[:dur_len]

In [58]:
ecg = pk.signal.resample_signal(ecg, sample_rate=sig_fs, target_rate=fs)
ppg1 = pk.signal.resample_signal(ppg1, sample_rate=sig_fs, target_rate=fs)
ppg2 = pk.signal.resample_signal(ppg2, sample_rate=sig_fs, target_rate=fs)
peaks = np.zeros(ecg.shape, dtype=int)
peaks[np.round(np.where(rr_peaks)[0]*(fs/sig_fs)).astype(int)] = 1

In [59]:
with open("/tmp/ecg.txt", "w") as f:
    for i in range(ecg.size):
        f.write(f"{ecg[i]:0.0f}, {os.linesep if i%40 == 39 else ''}")
with open("/tmp/ppg1.txt", "w") as f:
    for i in range(ecg.size):
        f.write(f"{ppg1[i]:0.0f}, {os.linesep if i%40 == 39 else ''}")
with open("/tmp/ppg2.txt", "w") as f:
    for i in range(ecg.size):
        f.write(f"{ppg2[i]:0.0f}, {os.linesep if i%40 == 39 else ''}")


In [60]:
ecg_clean = pk.ecg.clean(ecg, sample_rate=fs, lowcut=0.5, highcut=30.0)
qrs_clean = pk.ecg.clean(ecg, sample_rate=fs, lowcut=10.0, highcut=30.0)
pwave_clean = pk.ecg.clean(ecg, sample_rate=fs, lowcut=1.0, highcut=25.0)
ppg1_clean = pk.ppg.clean(ppg1, sample_rate=fs, lowcut=0.5, highcut=4.0)
ppg2_clean = pk.ppg.clean(ppg2, sample_rate=fs, lowcut=0.5, highcut=4.0) # (0.5, 1.5), (1.0, 2.0), (1.5, 2.5), (2.0, 3.0), (2.5, 3.5), (3.0, 4.0)

In [61]:
qrs_peaks, beg_qrs, end_qrs = pk.ecg.find_peaks(qrs_clean, sample_rate=fs)
qrs_rr_ints = pk.ecg.compute_rr_intervals(qrs_peaks, sample_rate=fs)
qrs_rr_mask = pk.ecg.filter_rr_intervals(qrs_rr_ints, sample_rate=fs)
filt_qrs_peaks = qrs_peaks[qrs_rr_mask == 0]
print(qrs_peaks)
print(qrs_rr_ints)
print(qrs_rr_mask)

[  53  234  487  732  963 1204 1464 1710 1950 2166 2383 2606 2842 3059
 3278 3507 3730 3948 4163 4394 4626 4846 5057 5274 5505 5731 5947 6170
 6368 6551 6735 6926 7119 7326]
[181 181 253 245 231 241 260 246 240 216 217 223 236 217 219 229 223 218
 215 231 232 220 211 217 231 226 216 223 198 183 184 191 193 207]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


In [62]:
ppg1_peaks = pk.ppg.find_peaks(ppg1_clean, sample_rate=fs)
ppg1_rr_ints = pk.ppg.compute_rr_intervals(ppg1_peaks, sample_rate=fs)
ppg1_rr_mask = pk.ppg.filter_rr_intervals(ppg1_rr_ints, sample_rate=fs)
ppg1_hr = pk.ppg.compute_heart_rate(ppg1_clean, sample_rate=fs)
filt_ppg1_peaks = ppg1_peaks[ppg1_rr_mask == 0]
print(ppg1_hr)
print(ppg1_peaks)
print(ppg1_rr_ints)
print(ppg1_rr_mask)

67.7490234375
[  28  271  523  771 1002 1241 1500 1748 1991 2208 2421 2643 2881 3099
 3316 3546 3770 3986 4201 4432 4665 4888 5096 5312 5543 5771 5987 6208
 6407 6589 6772 6962 7155 7362]
[243 243 252 248 231 239 259 248 243 217 213 222 238 218 217 230 224 216
 215 231 233 223 208 216 231 228 216 221 199 182 183 190 193 207]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


In [63]:
ppg2_peaks = pk.ppg.find_peaks(ppg2_clean, sample_rate=fs)
ppg2_rr_ints = pk.ppg.compute_rr_intervals(ppg2_peaks, sample_rate=fs)
ppg2_rr_mask = pk.ppg.filter_rr_intervals(ppg2_rr_ints, sample_rate=fs)
ppg2_hr = pk.ppg.compute_heart_rate(ppg2_clean, sample_rate=fs)
filt_ppg2_peaks = ppg2_peaks[ppg2_rr_mask == 0]
print(ppg2_hr)
print(ppg2_peaks)
print(ppg2_rr_ints)
print(ppg2_rr_mask)

67.7490234375
[  28  270  523  771 1002 1240 1500 1747 1990 2208 2421 2643 2880 3099
 3315 3546 3770 3986 4201 4431 4665 4888 5096 5312 5543 5771 5986 6208
 6407 6590 6772 6962 7155 7362]
[242 242 253 248 231 238 260 247 243 218 213 222 237 219 216 231 224 216
 215 230 234 223 208 216 231 228 215 222 199 183 182 190 193 207]
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


In [64]:
x = np.arange(0, len(ppg1))
fig = go.Figure()
# fig.add_trace(go.Scatter(x=x, y=ecg-ecg.mean(), name='ECG Raw'))
fig.add_trace(go.Scatter(x=x, y=ecg_clean/22, name='ECG Clean'))
fig.add_trace(go.Scatter(x=x, y=qrs_clean/42, name='QRS Clean'))
fig.add_trace(go.Scatter(x=x, y=pwave_clean/42-qrs_clean/42, name='P-wave Clean'))
sig = pwave_clean.copy()
for l, r in zip(beg_qrs, end_qrs):
    sig[l:r] = np.interp(x[l:r], [l, r], [sig[l], sig[r]])
    fig.add_shape(type="line", x0=l, y0=-1, x1=r, y1=1, line=dict(color="Purple", width=3))
    # fig.add_trace(go.Scatter(x=x, y=qrs_grad-avg_grad, name='QRS Grad'))
fig.add_trace(go.Scatter(x=x, y=sig/42, name='AVG Grad'))

#fig.add_trace(go.Scatter(x=x[peaks == 1], y=ecg_clean[peaks == 1], mode='markers', name='RR Peaks'))
#fig.add_trace(go.Scatter(x=x[qrs_peaks], y=ecg_clean[qrs_peaks], mode='markers', name='QRS Peaks'))
# fig.add_trace(go.Scatter(x=x, y=ppg1_clean, name='PPG1 Clean'))
# fig.add_trace(go.Scatter(x=x, y=ppg2_clean, name='PPG2 Clean'))
# fig.add_trace(go.Scatter(x=x[ppg1_peaks], y=ppg1_clean[ppg1_peaks], mode='markers', name='PPG1 Peaks'))
# fig.add_trace(go.Scatter(x=x[filt_ppg2_peaks], y=ppg2_clean[filt_ppg2_peaks], mode='markers', name='PPG2 Peaks'))
fig.show()

In [ ]:
ppg1_clean = np.array([592.675781, 697.811218, 801.537170, 903.313721, 1002.620361, 1098.961304, 1191.870972, 1280.918091, 1365.709839, 1445.894775, 1521.165405, 1591.260132, 1655.964722, 1715.113037, 1768.587280, 1816.317871, 1858.282593, 1894.505249, 1925.054565, 1950.041626, 1969.617798, 1983.971069, 1993.323730, 1997.928467, 1998.064575, 1994.033936, 1986.156982, 1974.768921, 1960.215088, 1942.846680, 1923.017212, 1901.078125, 1877.375000, 1852.244263, 1826.009399, 1798.978149, 1771.439697, 1743.662231, 1715.890869, 1688.345947, 1661.221191, 1634.683228, 1608.870239, 1583.891724, 1559.828247, 1536.731445, 1514.624634, 1493.502930, 1473.334961, 1454.063110, 1435.605591, 1417.857300, 1400.691895, 1383.963379, 1367.508423, 1351.148560, 1334.692627, 1317.939209, 1300.679443, 1282.699829, 1263.785034, 1243.721191, 1222.298950, 1199.316284, 1174.582031, 1147.918335, 1119.163940, 1088.177124, 1054.837646, 1019.049622, 980.743225, 939.876465, 896.436768, 850.441772, 801.939819, 751.010132, 697.762756, 642.337585, 584.903198, 525.655334, 464.815033, 402.626312, 339.353577, 275.278839, 210.698624, 145.920959, 81.261749, 17.041786, -46.416985, -108.794762, -169.777237, -229.058975, -286.346405, -341.360931, -393.841766, -443.548248, -490.262665, -533.791626, -573.968262, -610.653259, -643.736267, -673.136536, -698.803345, -720.715881, -738.883301, -753.343750, -764.164124, -771.438171, -775.285522, -775.850159, -773.298157, -767.815918, -759.608215, -748.895203, -735.911133, -720.901245, -704.119568, -685.826355, -666.285645, -645.763306, -624.524231, -602.830566, -580.939148, -559.099976, -537.554077, -516.531738, -496.251099, -476.916565, -458.717468, -441.827209, -426.401978, -412.579926, -400.480591, -390.204346, -381.832062, -375.424957, -371.024689, -368.653625, -368.314941, -369.993469, -373.656342, -379.253693, -386.719788, -395.973846, -406.921265, -419.454865, -433.455902, -448.795624, -465.336182, -482.932220, -501.431976, -520.678650, -540.511719, -560.767822, -581.282166, -601.889709, -622.425842, -642.727844, -662.635254, -681.990906, -700.641663, -718.439026, -735.239563, -750.905823, -765.306335, -778.316345, -789.817932, -799.700562, -807.861633, -814.206543, -818.649109, -821.111877, -821.526428, -819.833740, -815.984558, -809.939636, -801.669922, -791.156860, -778.392639, -763.380249, -746.133606, -726.677490, -705.047485, -681.289734, -655.460815, -627.627380, -597.865784, -566.261475, -532.908569, -497.908905, -461.371674, -423.412567, -384.152893, -343.718781, -302.240356, -259.850952, -216.686264, -172.883621, -128.581146, -83.917130, -39.029396, 5.945347, 50.872009, 95.617500, 140.051163, 184.044998, 227.473831, 270.215363, 312.150330, 353.162262, 393.137756, 431.966125, 469.539368, 505.752380, 540.502747, 573.690979, 605.220459, 634.998047, 662.934387, 688.944275, 712.947083, 734.867737, 754.637146, 772.192871, 787.479858, 800.451294, 811.069153, 819.304810, 825.139771, 828.566040, 829.586426, 828.214966, 824.476868, 818.408569, 810.057617, 799.482483, 786.751892, 771.944641, 755.148865, 736.461121, 715.986084, 693.835266, 670.126526, 644.983154, 618.532959, 590.907654, 562.241943, 532.673035, 502.339874, 471.382660, 439.942566, 408.161163, 376.180176, 344.141357, 312.186249, 280.455994, 249.091217, 218.231934, 188.017303, 158.585419, 130.072968, 102.614822, 76.343498, 51.388538, 27.875732, 5.926258, -14.344358, -32.827332, -49.421825, -64.036224, -76.589531, -87.012672, -95.249924, -101.260223, -105.018394, -106.516388, -105.764198, -102.790802, -97.644737, -90.394493, -81.128708, -69.955956, -57.004349, -42.420826, -26.370073, -9.033278, 9.393459, 28.700941, 48.668915, 69.068291, 89.663544, 110.215233, 130.482574, 150.226105, 169.210281, 187.206100, 203.993576, 219.364136, 233.122879, 245.090576, 255.105469, 263.024994, 268.727051, 272.111206, 273.099518, 271.637085, 267.692474, 261.257690, 252.348038, 241.001648, 227.278854, 211.261337, 193.051025, 172.768890, 150.553558, 126.559860, 100.957123, 73.927528, 45.664276, 16.369715, -13.746572, -44.469761, -75.581802, -106.863426, -138.096207, -169.064560, -199.557755, -229.371826, -258.311432, -286.191498, -312.838989, -338.094177, -361.811981, -383.863068, -404.134979, -422.532684, -438.979309, -453.416473, -465.804596, -476.122742, -484.368683, -490.558472, -494.725922, -496.922028, -497.214233, -495.685455, -492.433105, -487.567902, -481.212738, -473.501312, -464.576752, -454.590424, -443.700165, -432.068878, -419.863129, -407.251465, -394.402924, -381.485474, -368.664551, -356.101593, -343.952576, -332.366791, -321.485504, -311.440857, -302.354675, -294.337677, -287.488495, -281.892853, -277.623077, -274.737518, -273.280090, -273.280029, -274.751740, -277.694763, -282.093811, -287.919037, -295.126373, -303.657898, -313.442505, -324.396423, -336.424072, -349.418915, -363.264374, -377.834778, -392.996582, -408.609497, -424.527771, -440.601471, -456.677826, -472.602539, -488.221344, -503.381256, -517.931885, -531.726868, -544.625244, -556.492493, -567.201965, -576.635681, -584.685486, -591.254028, -596.255310, -599.615479, -601.273071, -601.179504, -599.299011, -595.608887, -590.099426, -582.773499, -573.646179, -562.744507, -550.106812, -535.781982, -519.829041, -502.316437, -483.321289, -462.928680, -441.230927, -418.326874, -394.321259, -369.324066, -343.449738, -316.816620, -289.546234, -261.762726, -233.592026, -205.161224, -176.597885, -148.029282, -119.581696, -91.379692, -63.545361, -36.197636, -9.451447, 16.582832, 41.800076, 66.101089, 89.393227, 111.590836, 132.615707, 152.397629, 170.874725, 187.993790, 203.710587, 217.990036, 230.806412, 242.143509, 251.994614, 260.362610, 267.259766, 272.707703, 276.737274, 279.388092, 280.708466, 280.754974, 279.592102, 277.291840, 273.933136, 269.601593, 264.388794, 258.391785, 251.712494, 244.457169, 236.735687, 228.660858, 220.347672, 211.912628, 203.472855, 195.145218, 187.045517, 179.287476, 171.981796, 165.235107, 159.149002, 153.818954, 149.333359, 145.772461, 143.207474, 141.699692, 141.299759, 142.047073, 143.969193, 147.081604, 151.387558, 156.878113, 163.532288, 171.317581, 180.190460, 190.097061, 200.974091, 212.749771, 225.344955, 238.674164, 252.646759, 267.168152, 282.140869, 297.465729, 313.042755, 328.772247, 344.555756, 360.296631, 375.900909, 391.277893, 406.340485, 421.005707, 435.195068, 448.834595, 461.855255, 474.192871, 485.788300, 496.587585, 506.541840, 515.607239, 523.745117, 530.921753, 537.108704, 542.282227, 546.423584, 549.518860, 551.558716, 552.538696, 552.458679, 551.322876, 549.139954, 545.922668, 541.688049, 536.456726, 530.253479, 523.106750, 515.048462, 506.114136, 496.342499, 485.775482, 474.457886, 462.437378, 449.764069, 436.490295, 422.670349, 408.360168, 393.617065, 378.499390, 363.066132, 347.376556, 331.489899, 315.465057, 299.360199, 283.232452, 267.137573, 251.129822, 235.261597, 219.583252, 204.142807, 188.985779, 174.155014, 159.690460, 145.629028, 132.004456, 118.847145, 106.184067, 94.038689, 82.430885, 71.376900, 60.889286, 50.976849, 41.644638, 32.893852, 24.721819, 17.121990, 10.083888, 3.593189, -2.368223, -7.822158, -12.793921, -17.312128, -21.408447, -25.117218, -28.475143, -31.520790, -34.294209, -36.836399, -39.188763, -41.392670, -43.488991, -45.517578, -47.516853, -49.523453, -51.571896, -53.694267, -55.920078, -58.276089, -60.786221, -63.471535, -66.350243, -69.437828, -72.747139, -76.288567, -80.070251, -84.098289, -88.376930, -92.908882, -97.695488, -102.736946, -108.032425, -113.580185, -119.377769, -125.421928, -131.708679, -138.233261, -144.990051, -151.972488, -159.173004, -166.582932, -174.192413, -181.990234, -189.963821, -198.099091, -206.380463, -214.790756, -223.311172, -231.921280, -240.599045, -249.320847, -258.061554, -266.794556, -275.491943, -284.124481, -292.661774, -301.072418, -309.324158, -317.384064, -325.218658, -332.794250, -340.076996, -347.033295, -353.630005, -359.834564, -365.615326, -370.941742, -375.784515, -380.115967, -383.910126, -387.143036, -389.792755, -391.839661, -393.266510, -394.058533, -394.203705, -393.692627, -392.518738, -390.678284, -388.170532, -384.997650, -381.164856, -376.680267, -371.555023, -365.803223, -359.442017, -352.491455, -344.974487, -336.916931, -328.347412, -319.297211, -309.800262, -299.893066, -289.614532, -279.005829, -268.110321, -256.973297, -245.641800, -234.164368, -222.590790, -210.971725, -199.358414, -187.802216, -176.354233, -165.064835, -153.983170, -143.156738, -132.630890, -122.448341, -112.648727, -103.268227, -94.339149, -85.889587, -77.943176, -70.518875, -63.630825, -57.288254, -51.495499, -46.252068, -41.552776, -37.387962, -33.743710, -30.602169, -27.941921, -25.738352, -23.964052, -22.589262, -21.582283, -20.909950, -20.538086, -20.431896, -20.556444, -20.877062, -21.359741, -21.971537, -22.680927, -23.458143, -24.275467, -25.107437, -25.931032, -26.725855, -27.474157, -28.160915, -28.773794, -29.303106, -29.741695, -30.084835, -30.330057, -30.476934, -30.526861, -30.482824, -30.349092, -30.130985, -29.834547, -29.466246, -29.032652, -28.540134, -27.994509, -27.400703, -26.762403, -26.081738, -25.358959, -24.592190, -23.777132, -22.906916, -21.971876, -20.959494, -19.854294, -18.637886, -17.288998, -15.783621, -14.095195, -12.194832, -10.051614, -7.632913, -4.904761, -1.832274, 1.619926, 5.487227, 9.804504, 14.605641, 19.922935, 25.786575, 32.224060, 39.259640, 46.913715, 55.202309, 64.136536, 73.722122, 83.958939, 94.840668, 106.354446, 118.480598, 131.192474, 144.456299, 158.231125, 172.468948, 187.114731, 202.106750, 217.376831, 232.850723, 248.448685, 264.085907, 279.673218, 295.117645, 310.323303, 325.192230, 339.624969, 353.521759, 366.783356, 379.312134, 391.013000, 401.794281, 411.568939, 420.255493, 427.778809, 434.070984, 439.072296, 442.731842, 445.008209, 445.870087, 445.296570, 443.277588, 439.814270, 434.918823, 428.614410, 420.935150, 411.925873, 401.641602, 390.146973, 377.515747, 363.830048, 349.179535, 333.660492, 317.374908, 300.429382, 282.934174, 265.002045, 246.747223, 228.284225, 209.726868, 191.187180, 172.774368, 154.593887, 136.746506, 119.327454, 102.425591, 86.122704, 70.492859, 55.601826, 41.506653, 28.255280, 15.886317, 4.428869, -6.097479, -15.682625, -24.325712, -32.034920, -38.827110, -44.727337, -49.768425, -53.990307, -57.439442, -60.168087, -62.233578, -63.697544, -64.625084, -65.083916, -65.143555, -64.874527, -64.347527, -63.632599, -62.798378, -61.911442, -61.035568, -60.231167, -59.554787, -59.058601, -58.790051, -58.791531, -59.100090, -59.747276, -60.758945, -62.155178, -63.950203, -66.152382, -68.764275, -71.782661, -75.198685, -78.997955, -83.160835, -87.662605, -92.473793, -97.560509, -102.884842, -108.405266, -114.077148, -119.853233, -125.684174, -131.519104, -137.306168, -142.993088, -148.527725, -153.858582, -158.935394, -163.709671, -168.135162, -172.168320, -175.768768, -178.899643, -181.527908, -183.624527, -185.164734, -186.128006, -186.498138, -186.263168, -185.415344, -183.950928, -181.870087, -179.176773, -175.878494, -171.986145, -167.513870, -162.478897, -156.901382, -150.804260, -144.213165, -137.156250, -129.664078, -121.769501, -113.507553, -104.915215, -96.031311, -86.896286, -77.551918, -68.041130, -58.407658, -48.695724, -38.949745, -29.213963, -19.532104, -9.947029, -0.500389, 8.767692, 17.818926, 26.617140, 35.128525, 43.321846, 51.168648, 58.643410, 65.723656, 72.390030, 78.626366, 84.419678, 89.760101, 94.640869, 99.058205, 103.011253, 106.501884, 109.534554, 112.116127, 114.255669, 115.964249, 117.254700, 118.141396, 118.639984, 118.767166, 118.540413, 117.977768, 117.097626, 115.918518, 114.459007, 112.737488, 110.772118, 108.580727, 106.180771, 103.589272, 100.822845, 97.897682, 94.829582, 91.633972, 88.325974, 84.920380, 81.431725, 77.874268, 74.262039, 70.608856, 66.928352, 63.234020, 59.539215, 55.857220, 52.201233, 48.584431, 45.019989, 41.521107, 38.101032, 34.773079, 31.550629, 28.447155, 25.476198, 22.651365, 19.986298, 17.494633, 15.189960, 13.085741, 11.195238, 9.531384, 8.106647, 6.932887, 6.021149, 5.381499, 5.022814, 4.952576, 5.176684, 5.699263, 6.522467, 7.646327, 9.068602, 10.784632, 12.787245, 15.066683, 17.610563, 20.403887, 23.429075, 26.666063, 30.092417, 33.683498, 37.412670, 41.251530, 45.170181, 49.137527, 53.121609, 57.089966, 61.010006, 64.849380, 68.576370, 72.160255, 75.571671, 78.782944, 81.768341, 84.504333, 86.969772, 89.145996, 91.016869, 92.568748, 93.790443, 94.673058, 95.209831, 95.395927, 95.228165, 94.704735, 93.824921, 92.588799, 90.996925, 89.050102, 86.749130, 84.094620, 81.086861, 77.725769, 74.010872, 69.941360, 65.516258, 60.734585, 55.595608, 50.099113, 44.245701, 38.037098, 31.476442, 24.568575, 17.320309, 9.740662, 1.841050, -6.364560, -14.859544, -23.624563, -32.637554, -41.873756, -51.305756, -60.903622, -70.635010, -80.465294, -90.357727, -100.273590, -110.172386, -120.012016, -129.748993, -139.338699, -148.735703, -157.893951, -166.767242, -175.309509, -183.475220, -191.219818, -198.500168, -205.274948, -211.505142, -217.154434, -222.189651, -226.581177, -230.303238, -233.334274, -235.657150, -237.259445, -238.133575, -238.276901, -237.691696, -236.385254, -234.369751, -231.662201, -228.284180, -224.261719, -219.624969, -214.407928, -208.648102, -202.386185, -195.665604, -188.532181, -181.033691, -173.219513, -165.140152, -156.846817, -148.390945, -139.823837, -131.196182, -122.557747, -113.956932, -105.440414, -97.052803, -88.836311, -80.830444, -73.071724, -65.593460, -58.425545, -51.594276, -45.122257, -39.028316, -33.327469, -28.030912, -23.146069, -18.676670, -14.622869, -10.981384, -7.745652, -4.906051, -2.450095, -0.362669, 1.373687, 2.778530, 3.873191, 4.680507, 5.224464, 5.529893, 5.622164, 5.526850, 5.269450, 4.875100, 4.368344, 3.772907, 3.111561, 2.405940, 1.676486, 0.942371, 0.221429, -0.469824, -1.116240, -1.704018, -2.220723, -2.655295, -2.998026, -3.240586, -3.376017, -3.398752, -3.304622, -3.090875, -2.756164, -2.300528, -1.725333, -1.033203, -0.227903, 0.685780, 1.702213, 2.815070, 4.017540, 5.302497, 6.662694, 8.090933, 9.580210, 11.123851, 12.715597, 14.349686, 16.020908, 17.724588, 19.456589, 21.213238, 22.991282, 24.787779, 26.599993, 28.425293, 30.261023, 32.104420, 33.952488, 35.801952, 37.649158, 39.490032, 41.320038, 43.134174, 44.926933, 46.692360, 48.424038, 50.115170, 51.758636, 53.347076, 54.872967, 56.328705, 57.706715, 58.999508, 60.199795, 61.300529, 62.295006, 63.176914, 63.940414, 64.580185, 65.091492, 65.470207, 65.712860, 65.816681, 65.779663, 65.600601, 65.279099, 64.815598, 64.211395, 63.468616, 62.590210, 61.579880, 60.442085, 59.181938, 57.805202, 56.318195, 54.727749, 53.041145, 51.266094, 49.410690, 47.483395, 45.493004, 43.448643, 41.359749, 39.236027, 37.087421, 34.924076, 32.756287, 30.594439, 28.448931, 26.330084, 24.248051, 22.212708, 20.233557, 18.319620, 16.479336, 14.720484, 13.050078, 11.474300, 9.998411, 8.626680, 7.362320, 6.207431, 5.162961, 4.228686, 3.403206, 2.683947, 2.067180, 1.548056, 1.120648, 0.778021, 0.512302, 0.314780, 0.176012, 0.085945, 0.034058, 0.009515, 0.001356, ])
ppg2_clean = np.array([211.753845, 268.251221, 324.082581, 378.957367, 432.594635, 484.726563, 535.101013, 583.483826, 629.661194, 673.440979, 714.654358, 753.156494, 788.827454, 821.572632, 851.322876, 878.034302, 901.687866, 922.288757, 939.865601, 954.469299, 966.171692, 975.064209, 981.255981, 984.872253, 986.052490, 984.948547, 981.722412, 976.544250, 969.590454, 961.041382, 951.079529, 939.887512, 927.646118, 914.532654, 900.719177, 886.370972, 871.645203, 856.689453, 841.640869, 826.625061, 811.755310, 797.131836, 782.841553, 768.957458, 755.538635, 742.630066, 730.262939, 718.454468, 707.208496, 696.515869, 686.354980, 676.692444, 667.483765, 658.674133, 650.199585, 641.987488, 633.958130, 626.025513, 618.098816, 610.083557, 601.882813, 593.398804, 584.534180, 575.193481, 565.284485, 554.719788, 543.417847, 531.304565, 518.314331, 504.391296, 489.490173, 473.577209, 456.630768, 438.641937, 419.614929, 399.567169, 378.529297, 356.545044, 333.670715, 309.974762, 285.536926, 260.447479, 234.806137, 208.721024, 182.307373, 155.686340, 128.983658, 102.328239, 75.850800, 49.682369, 23.952972, -1.209862, -25.682344, -49.345692, -72.087494, -93.802757, -114.394936, -133.776886, -151.871613, -168.613068, -183.946564, -197.829193, -210.230194, -221.130920, -230.524994, -238.417938, -244.827133, -249.781204, -253.319702, -255.492371, -256.358429, -255.985931, -254.450867, -251.836227, -248.231094, -243.729660, -238.430359, -232.434814, -225.846985, -218.772064, -211.315735, -203.583221, -195.678452, -187.703186, -179.756439, -171.933609, -164.325851, -157.019424, -150.095093, -143.627777, -137.685883, -132.331131, -127.618019, -123.593575, -120.297287, -117.760788, -116.007896, -115.054688, -114.909439, -115.572838, -117.038269, -119.292053, -122.313713, -126.076424, -130.547394, -135.688263, -141.455505, -147.800995, -154.672394, -162.013779, -169.765976, -177.867111, -186.253159, -194.858414, -203.615921, -212.458008, -221.316727, -230.124283, -238.813492, -247.318024, -255.572922, -263.514801, -271.082214, -278.215912, -284.858978, -290.957275, -296.459473, -301.317474, -305.486328, -308.924530, -311.594330, -313.461792, -314.496826, -314.673584, -313.970398, -312.369995, -309.859528, -306.430725, -302.079895, -296.808014, -290.620728, -283.528168, -275.544983, -266.690277, -256.987488, -246.464096, -235.151459, -223.084656, -210.302170, -196.845551, -182.759201, -168.090012, -152.886993, -137.200989, -121.084305, -104.590401, -87.773537, -70.688515, -53.390316, -35.933914, -18.373957, -0.764583, 16.840784, 34.389584, 51.830242, 69.112259, 86.186241, 103.003960, 119.518333, 135.683426, 151.454376, 166.787323, 181.639496, 195.969131, 209.735428, 222.898651, 235.420181, 247.262558, 258.389648, 268.766907, 278.361450, 287.142395, 295.081146, 302.151581, 308.330444, 313.597626, 317.936371, 321.333618, 323.780182, 325.270966, 325.805145, 325.386261, 324.022339, 321.725800, 318.513489, 314.406525, 309.430145, 303.613678, 296.990112, 289.595947, 281.470825, 272.657318, 263.200500, 253.147751, 242.548340, 231.453171, 219.914474, 207.985580, 195.720627, 183.174438, 170.402298, 157.459839, 144.402939, 131.287643, 118.170082, 105.106415, 92.152786, 79.365265, 66.799767, 54.511971, 42.557167, 30.990103, 19.864746, 9.234054, -0.850352, -10.338528, -19.182613, -27.337248, -34.760067, -41.412205, -47.258770, -52.269455, -56.419003, -59.687733, -62.062027, -63.534737, -64.105621, -63.781662, -62.577286, -60.514530, -57.623131, -53.940460, -49.511410, -44.388107, -38.629574, -32.301277, -25.474522, -18.225805, -10.636089, -2.789980, 5.225160, 13.320098, 21.404680, 29.388773, 37.183201, 44.700687, 51.856739, 58.570518, 64.765633, 70.370895, 75.320999, 79.557114, 83.027412, 85.687508, 87.500786, 88.438652, 88.480721, 87.614838, 85.837112, 83.151810, 79.571190, 75.115265, 69.811516, 63.694538, 56.805653, 49.192463, 40.908363, 32.012005, 22.566730, 12.639975, 2.302626, -8.371653, -19.307096, -30.426569, -41.652279, -52.906521, -64.112396, -75.194542, -86.079819, -96.698006, -106.982384, -116.870346, -126.303947, -135.230362, -143.602264, -151.378235, -158.523087, -165.008026, -170.810822, -175.915909, -180.314438, -184.004150, -186.989395, -189.280807, -190.895142, -191.855011, -192.188446, -191.928635, -191.113419, -189.784866, -187.988739, -185.774063, -183.192551, -180.298080, -177.146118, -173.793152, -170.296219, -166.712234, -163.097549, -159.507401, -155.995377, -152.612900, -149.408813, -146.429016, -143.716003, -141.308517, -139.241287, -137.544769, -136.244873, -135.362839, -134.915054, -134.912979, -135.363068, -136.266739, -137.620468, -139.415741, -141.639236, -144.272858, -147.294006, -150.675720, -154.386932, -158.392731, -162.654633, -167.130936, -171.777115, -176.546188, -181.389145, -186.255371, -191.093140, -195.850082, -200.473663, -204.911713, -209.112900, -213.027206, -216.606415, -219.804642, -222.578720, -224.888672, -226.698029, -227.974182, -228.688721, -228.817566, -228.341202, -227.244827, -225.518356, -223.156448, -220.158478, -216.528427, -212.274734, -207.410095, -201.951248, -195.918747, -189.336639, -182.232208, -174.635696, -166.579956, -158.100220, -149.233749, -140.019623, -130.498474, -120.712234, -110.703865, -100.517181, -90.196579, -79.786819, -69.332809, -58.879349, -48.470943, -38.151524, -27.964241, -17.951221, -8.153333, 1.390030, 10.641148, 19.564190, 28.125378, 36.293179, 44.038403, 51.334316, 58.156837, 64.484566, 70.298889, 75.584030, 80.327095, 84.518166, 88.150314, 91.219612, 93.725197, 95.669228, 97.056923, 97.896523, 98.199287, 97.979500, 97.254379, 96.044037, 94.371437, 92.262276, 89.744926, 86.850319, 83.611816, 80.065117, 76.248108, 72.200729, 67.964676, 63.583347, 59.101463, 54.564899, 50.020355, 45.515106, 41.096588, 36.812073, 32.708263, 28.830872, 25.224182, 21.930593, 18.990156, 16.440115, 14.314471, 12.643573, 11.453734, 10.766892, 10.600318, 10.966410, 11.872533, 13.320956, 15.308828, 17.828285, 20.866570, 24.406267, 28.425581, 32.898655, 37.795921, 43.084549, 48.728825, 54.690643, 60.929947, 67.405167, 74.073685, 80.892273, 87.817474, 94.805946, 101.814835, 108.802048, 115.726517, 122.548431, 129.229446, 135.732803, 142.023605, 148.068802, 153.837357, 159.300369, 164.431152, 169.205292, 173.600784, 177.598068, 181.180069, 184.332245, 187.042648, 189.301941, 191.103348, 192.442703, 193.318359, 193.731293, 193.684952, 193.185287, 192.240677, 190.861832, 189.061798, 186.855820, 184.261230, 181.297394, 177.985474, 174.348343, 170.410461, 166.197678, 161.737015, 157.056427, 152.184677, 147.151047, 141.985153, 136.716660, 131.375061, 125.989464, 120.588348, 115.199341, 109.849022, 104.562744, 99.364471, 94.276619, 89.319946, 84.513443, 79.874222, 75.417450, 71.156303, 67.101898, 63.263271, 59.647354, 56.258991, 53.100952, 50.173981, 47.476837, 45.006363, 42.757561, 40.723682, 38.896301, 37.265419, 35.819561, 34.545876, 33.430256, 32.457439, 31.611139, 30.874182, 30.228647, 29.656027, 29.137373, 28.653475, 28.185022, 27.712776, 27.217749, 26.681370, 26.085659, 25.413383, 24.648220, 23.774895, 22.779310, 21.648647, 20.371458, 18.937721, 17.338882, 15.567857, 13.619031, 11.488214, 9.172590, 6.670659, 3.982143, 1.107900, -1.950171, -5.189225, -8.605576, -12.194778, -15.951694, -19.870564, -23.945047, -28.168282, -32.532883, -37.030975, -41.654182, -46.393627, -51.239929, -56.183186, -61.212944, -66.318214, -71.487434, -76.708496, -81.968727, -87.254929, -92.553406, -97.850021, -103.130219, -108.379105, -113.581474, -118.721901, -123.784782, -128.754410, -133.615036, -138.350922, -142.946442, -147.386063, -151.654465, -155.736588, -159.617661, -163.283279, -166.719467, -169.912796, -172.850342, -175.519791, -177.909592, -180.008942, -181.807907, -183.297455, -184.469574, -185.317352, -185.835022, -186.018066, -185.863220, -185.368546, -184.533493, -183.358932, -181.847168, -180.001938, -177.828461, -175.333420, -172.524963, -169.412704, -166.007706, -162.322418, -158.370697, -154.167709, -149.729950, -145.075089, -140.221939, -135.190414, -130.001404, -124.676712, -119.238968, -113.711517, -108.118279, -102.483665, -96.832428, -91.189491, -85.579811, -80.028206, -74.559135, -69.196526, -63.963577, -58.882549, -53.974556, -49.259365, -44.755184, -40.478477, -36.443787, -32.663574, -29.148109, -25.905369, -22.940964, -20.258110, -17.857624, -15.737946, -13.895194, -12.323259, -11.013906, -9.956903, -9.140156, -8.549884, -8.170778, -7.986184, -7.978283, -8.128300, -8.416689, -8.823341, -9.327790, -9.909422, -10.547678, -11.222260, -11.913316, -12.601619, -13.268737, -13.897186, -14.470572, -14.973718, -15.392760, -15.715247, -15.930192, -16.028135, -16.001183, -15.843025, -15.548941, -15.115786, -14.541964, -13.827382, -12.973391, -11.982699, -10.859288, -9.608294, -8.235894, -6.749152, -5.155865, -3.464404, -1.683501, 0.177933, 2.111006, 4.107041, 6.157765, 8.255473, 10.393195, 12.564830, 14.765264, 16.990475, 19.237593, 21.504963, 23.792149, 26.099922, 28.430239, 30.786163, 33.171783, 35.592106, 38.052925, 40.560692, 43.122326, 45.745071, 48.436306, 51.203354, 54.053276, 56.992683, 60.027542, 63.162964, 66.403015, 69.750549, 73.207024, 76.772377, 80.444878, 84.221039, 88.095528, 92.061073, 96.108452, 100.226448, 104.401886, 108.619667, 112.862862, 117.112740, 121.348984, 125.549774, 129.691971, 133.751358, 137.702774, 141.520401, 145.178009, 148.649261, 151.907959, 154.928375, 157.685547, 160.155579, 162.315933, 164.145737, 165.626068, 166.740173, 167.473740, 167.815094, 167.755356, 167.288635, 166.412140, 165.126266, 163.434662, 161.344269, 158.865250, 156.010895, 152.797607, 149.244736, 145.374359, 141.211136, 136.781998, 132.115936, 127.243690, 122.197403, 117.010300, 111.716354, 106.349907, 100.945328, 95.536621, 90.157112, 84.839081, 79.613480, 74.509613, 69.554878, 64.774521, 60.191399, 55.825806, 51.695282, 47.814499, 44.195148, 40.845882, 37.772278, 34.976837, 32.459034, 30.215384, 28.239532, 26.522398, 25.052315, 23.815210, 22.794823, 21.972914, 21.329508, 20.843157, 20.491201, 20.250055, 20.095484, 20.002872, 19.947512, 19.904873, 19.850883, 19.762171, 19.616306, 19.392033, 19.069460, 18.630243, 18.057758, 17.337214, 16.455772, 15.402607, 14.168987, 12.748291, 11.136043, 9.329912, 7.329701, 5.137322, 2.756784, 0.194144, -2.542555, -5.443328, -8.496290, -11.687762, -15.002338, -18.422987, -21.931149, -25.506891, -29.129055, -32.775417, -36.422878, -40.047680, -43.625626, -47.132305, -50.543316, -53.834473, -56.982063, -59.963108, -62.755554, -65.338524, -67.692505, -69.799545, -71.643425, -73.209778, -74.486206, -75.462372, -76.130020, -76.482994, -76.517258, -76.230858, -75.623840, -74.698212, -73.457863, -71.908485, -70.057457, -67.913811, -65.488129, -62.792480, -59.840366, -56.646671, -53.227627, -49.600746, -45.784767, -41.799622, -37.666332, -33.406967, -29.044537, -24.602875, -20.106539, -15.580660, -11.050792, -6.542745, -2.082416, 2.304401, 6.592197, 10.755931, 14.771212, 18.614473, 22.263147, 25.695820, 28.892389, 31.834202, 34.504177, 36.886929, 38.968857, 40.738235, 42.185257, 43.302105, 44.082973, 44.524082, 44.623707, 44.382168, 43.801823, 42.887051, 41.644199, 40.081558, 38.209278, 36.039280, 33.585155, 30.862047, 27.886536, 24.676510, 21.251040, 17.630232, 13.835109, 9.887466, 5.809739, 1.624866, -2.643842, -6.972854, -11.338542, -15.717315, -20.085758, -24.420771, -28.699701, -32.900471, -37.001705, -40.982868, -44.824360, -48.507645, -52.015316, -55.331196, -58.440392, -61.329350, -63.985859, -66.399078, -68.559540, -70.459137, -72.091080, -73.449928, -74.531479, -75.332748, -75.851952, -76.088440, -76.042648, -75.716034, -75.111061, -74.231148, -73.080612, -71.664711, -69.989586, -68.062286, -65.890747, -63.483833, -60.851334, -58.003971, -54.953430, -51.712349, -48.294334, -44.713943, -40.986664, -37.128902, -33.157955, -29.091944, -24.949774, -20.751049, -16.515984, -12.265293, -8.020073, -3.801668, 0.368478, 4.468976, 8.478665, 12.376797, 16.143223, 19.758595, 23.204563, 26.463985, 29.521111, 32.361771, 34.973549, 37.345932, 39.470406, 41.340549, 42.952068, 44.302788, 45.392620, 46.223469, 46.799122, 47.125122, 47.208584, 47.058014, 46.683090, 46.094460, 45.303493, 44.322060, 43.162292, 41.836384, 40.356388, 38.734032, 36.980591, 35.106758, 33.122559, 31.037291, 28.859531, 26.597120, 24.257212, 21.846346, 19.370533, 16.835342, 14.246022, 11.607608, 8.925023, 6.203195, 3.447145, 0.662077, -2.146556, -4.972990, -7.811109, -10.654411, -13.495994, -16.328537, -19.144304, -21.935143, -24.692493, -27.407408, -30.070560, -32.672276, -35.202557, -37.651138, -40.007530, -42.261089, -44.401108, -46.416885, -48.297844, -50.033634, -51.614258, -53.030182, -54.272469, -55.332886, -56.204029, -56.879452, -57.353767, -57.622757, -57.683464, -57.534260, -57.174908, -56.606617, -55.832066, -54.855408, -53.682259, -52.319675, -50.776119, -49.061378, -47.186508, -45.163738, -43.006363, -40.728634, -38.345638, -35.873180, -33.327625, -30.725761, -28.084644, -25.421448, -22.753304, -20.097147, -17.469566, -14.886660, -12.363893, -9.915972, -7.556720, -5.298963, -3.154416, -1.133602, 0.754225, 2.501141, 4.100584, 5.547385, 6.837778, 7.969397, 8.941260, 9.753744, 10.408548, 10.908669, 11.258339, 11.462997, 11.529205, 11.464578, 11.277696, 10.977997, 10.575676, 10.081551, 9.506932, 8.863486, 8.163073, 7.417601, 6.638864, 5.838395, 5.027327, 4.216271, 3.415208, 2.633405, 1.879351, 1.160718, 0.484325, -0.143875, -0.718804, -1.236258, -1.692893, -2.086212, -2.414540, -2.676997, -2.873465, -3.004559, -3.071582, -3.076488, -3.021845, -2.910781, -2.746949, -2.534470, -2.277875, -1.982035, -1.652087, -1.293348, -0.911224, -0.511117, -0.098335, 0.321996, 0.745004, 1.166139, 1.581216, 1.986465, 2.378546, 2.754570, 3.112111, 3.449193, 3.764283, 4.056277, 4.324480, 4.568578, 4.788608, 4.984939, 5.158247, 5.309494, 5.439912, 5.550992, 5.644466, 5.722296, 5.786663, 5.839957, 5.884762, 5.923843, 5.960142, 5.996756, 6.036907, 6.083922, 6.141177, 6.212064, 6.299931, 6.408030, 6.539455, 6.697081, 6.883490, 7.100915, 7.351172, 7.635607, 7.955048, 8.309759, 8.699408, 9.123034, 9.579031, 10.065137, 10.578424, 11.115297, 11.671515, 12.242194, 12.821849, 13.404427, 13.983360, 14.551651, 15.101946, 15.626639, 16.117994, 16.568262, 16.969833, 17.315382, 17.598015, 17.811415, 17.949974, 18.008932, 17.984486, 17.873890, 17.675545, 17.389055, 17.015276, 16.556324, 16.015583, 15.397683, 14.708446, 13.954826, 13.144827, 12.287386, 11.392257, 10.469863, 9.531139, 8.587356, 7.649921, 6.730185, 5.839219, 4.987598, 4.185180, 3.440871, 2.762400, 2.156084, 1.626605, 1.176778, 0.807332, 0.516688, 0.300746, 0.152680, 0.062745, 0.018099, 0.002647, ])
qrs_clean = np.array([-1829.487793, -3607.830322, -4336.834473, -4000.844727, -2922.430176, -1570.928223, -377.278809, 388.257172, 658.508362, 539.778503, 243.204559, 8.393877, 24.677361, 352.879822, 886.059753, 1399.366943, 1674.265503, 1606.450317, 1226.600342, 650.484924, 15.736554, -560.342529, -993.875366, -1224.982666, -1210.012695, -941.039795, -482.353241, 25.208122, 421.391663, 604.544861, 563.783264, 353.355194, 49.399555, -278.040131, -570.342834, -767.742249, -798.309143, -598.468506, -168.994766, 381.828644, 867.971985, 1122.457397, 1082.106934, 797.277039, 380.700409, -53.813641, -428.701965, -703.435547, -847.747437, -822.386963, -599.713013, -210.369537, 238.330658, 604.579956, 781.115723, 733.224670, 491.436920, 124.161888, -287.840057, -664.137756, -921.081970, -970.166443, -747.771729, -272.708801, 321.453583, 830.922974, 1086.018066, 1035.126343, 748.810242, 357.769867, -23.141111, -339.646484, -587.636169, -762.181702, -820.284973, -701.278625, -388.058838, 51.914482, 485.956757, 776.767639, 837.101624, 653.477051, 279.754303, -188.986694, -641.662354, -960.216187, -1029.849731, -780.025940, -244.881943, 413.345337, 961.025757, 1207.068604, 1097.007935, 724.670471, 262.509155, -139.560242, -423.165161, -613.432007, -748.017151, -814.423523, -753.607361, -518.530640, -129.923782, 315.092255, 681.807678, 854.678711, 781.121033, 482.843872, 36.383446, -450.245667, -845.592773, -1009.400269, -843.825256, -361.978485, 285.636932, 864.113098, 1164.093506, 1102.020874, 749.515198, 277.701355, -146.190323, -441.100494, -616.695862, -710.554688, -728.437134, -640.263977, -420.305237, -87.938667, 281.915070, 583.810120, 726.194580, 667.510071, 421.626038, 38.934113, -403.819489, -792.970764, -983.973938, -858.643677, -405.623199, 242.111191, 850.716614, 1192.545898, 1157.552368, 802.022827, 302.985687, -152.182938, -462.370819, -627.414185, -689.672058, -673.752563, -573.457825, -376.264923, -94.778603, 217.078094, 476.815338, 610.374817, 583.950378, 403.845825, 96.555145, -291.459900, -668.370300, -894.289917, -837.849304, -460.110107, 139.066254, 748.121765, 1136.497803, 1167.816162, 865.576416, 384.477112, -92.562782, -451.104309, -665.895691, -755.424194, -735.421326, -608.922668, -381.395081, -80.992065, 230.711945, 474.081635, 589.695801, 564.269226, 416.779694, 167.811569, -159.427399, -503.539185, -750.004333, -775.324341, -521.089966, -42.549942, 498.560669, 900.171631, 1019.640320, 845.874146, 487.281982, 86.005348, -264.473053, -533.362793, -712.480103, -782.708191, -715.576599, -496.721588, -154.503174, 225.724991, 528.253174, 667.346375, 627.125793, 443.469421, 159.587006, -184.878128, -525.284485, -757.917236, -775.937988, -529.841858, -68.843849, 460.263458, 867.230591, 1011.230469, 873.174438, 546.973267, 159.713760, -202.379166, -503.477783, -722.609924, -828.703552, -785.993347, -576.126282, -226.482224, 173.741486, 501.789642, 667.261841, 654.241821, 499.269867, 242.706848, -82.638977, -421.656433, -679.961731, -752.627930, -576.780396, -174.960144, 331.371826, 760.635681, 960.642212, 888.222046, 610.430359, 234.958466, -154.296021, -504.580688, -768.399902, -893.006042, -834.616760, -581.792419, -181.170441, 253.067566, 579.914795, 709.593689, 646.428284, 454.647980, 194.516464, -99.145294, -390.027863, -616.578918, -702.647705, -589.400818, -271.752655, 173.840790, 602.807922, 872.579224, 917.454041, 758.754272, 454.622314, 58.567627, -373.961731, -762.968506, -1008.815308, -1023.951538, -771.601868, -302.590546, 235.224350, 654.096802, 828.857117, 755.213135, 514.518738, 197.976089, -130.644623, -422.851013, -627.637207, -692.969971, -579.249023, -283.035828, 133.633469, 545.795105, 824.350830, 903.414978, 788.933350, 515.797913, 119.926643, -345.462036, -787.676453, -1085.970215, -1130.349854, -868.339661, -350.737701, 256.268097, 738.230225, 951.435730, 889.943848, 645.648865, 321.208069, -17.185621, -331.863861, -589.761047, -747.037659, -746.653748, -543.874084, -158.147186, 302.932495, 692.530640, 902.742737, 893.626648, 669.555298, 262.717682, -252.735443, -752.789917, -1090.272339, -1141.204712, -853.124878, -290.680908, 356.076721, 849.611267, 1036.683594, 920.362427, 614.843994, 248.114624, -96.943359, -384.716064, -603.908630, -739.115112, -749.480164, -584.493774, -241.324234, 197.283249, 598.668335, 850.924500, 893.442749, 705.196411, 304.264832, -229.944656, -753.763489, -1097.916260, -1125.418579, -787.735352, -170.751816, 507.422150, 990.733826, 1127.013428, 937.228577, 560.229492, 145.994431, -210.513504, -476.771088, -658.804993, -763.034546, -762.583862, -607.121765, -282.753448, 143.113037, 549.958252, 828.889771, 911.330139, 761.654602, 384.363312, -149.018387, -696.286194, -1082.069458, -1154.179443, -843.614197, -221.098785, 495.301727, 1033.255005, 1215.575806, 1040.890259, 639.102295, 170.051590, -247.739120, -558.634338, -758.036987, -855.183716, -832.794128, -651.262146, -305.893951, 131.189728, 542.504028, 829.169250, 933.382874, 823.542725, 496.393158, 2.864782, -541.958801, -980.902527, -1155.005127, -961.016663, -423.287109, 275.318909, 869.072083, 1155.635620, 1088.950684, 756.656677, 298.908295, -156.414932, -524.949402, -770.511108, -881.074524, -835.689880, -610.054749, -226.830551, 216.845276, 594.157532, 816.209290, 848.491211, 686.258240, 346.396240, -116.105812, -601.229858, -977.864075, -1109.563721, -901.808533, -372.890717, 309.651550, 896.141785, 1192.307739, 1148.097778, 839.162170, 394.182312, -65.166100, -456.888153, -744.916199, -912.716064, -927.896912, -750.179932, -387.882813, 67.931297, 484.329651, 756.291077, 832.114563, 698.988220, 377.865051, -66.538979, -527.491089, -873.548096, -973.621216, -743.709412, -215.595398, 433.675995, 955.812500, 1168.238525, 1036.349121, 650.617126, 154.296982, -316.893005, -671.608093, -873.815857, -919.185486, -801.547974, -518.659241, -115.990028, 299.262665, 611.621521, 760.954956, 747.286560, 593.421936, 323.194580, -32.849407, -425.412781, -774.136292, -963.003113, -876.048645, -480.261322, 113.209503, 689.585999, 1050.015137, 1102.991455, 871.319519, 451.236206, -32.564793, -467.779816, -779.641907, -923.231628, -864.601990, -595.911560, -177.827438, 257.517395, 572.997192, 699.453247, 645.100708, 456.274017, 184.369232, -125.574127, -433.776794, -689.774963, -813.808044, -717.224182, -372.941376, 129.531784, 617.705688, 935.404175, 1013.244324, 866.957825, 560.970642, 174.514008, -224.416290, -586.287598, -858.143250, -964.642151, -839.315369, -491.227539, -30.079473, 389.735138, 650.899292, 708.452393, 577.257385, 308.727478, -30.504736, -374.531097, -654.200562, -783.479004, -679.654968, -327.807495, 173.509338, 650.898499, 952.908447, 1015.627380, 858.500488, 546.808411, 156.510925, -250.681763, -629.094238, -922.184509, -1045.053223, -921.873169, -557.575317, -65.537537, 388.264923, 673.041443, 739.731750, 614.214783, 365.244598, 65.809311, -232.609421, -489.770538, -646.491638, -628.336060, -400.264618, -15.758527, 400.999451, 724.263000, 879.178467, 847.658264, 651.474426, 332.483795, -65.091560, -493.147766, -873.690857, -1089.324951, -1032.853516, -689.154053, -169.272354, 343.282990, 687.153076, 786.643982, 660.995789, 393.762482, 80.828232, -210.897186, -441.024933, -565.151917, -531.656616, -323.160065, 7.400826, 355.641144, 621.871338, 748.839478, 721.983521, 554.690674, 273.517700, -92.027199, -499.230682, -863.562012, -1057.270386, -970.339844, -595.646912, -57.274738, 450.730133, 764.467163, 817.248352, 647.327148, 357.418884, 50.046951, -218.448883, -428.864471, -557.184753, -561.159668, -414.614685, -143.754471, 179.365280, 474.873932, 683.255554, 769.070374, 714.318787, 510.579285, 157.975006, -311.625244, -797.375488, -1131.934326, -1156.787354, -825.077332, -246.377426, 365.196808, 798.259216, 935.414429, 786.584167, 458.395233, 81.757996, -249.890900, -487.787231, -599.186707, -558.150146, -369.238037, -84.112259, 218.738281, 471.831665, 637.612793, 700.837280, 651.550720, 472.352509, 143.773712, -317.796234, -812.556885, -1161.894287, -1192.913940, -849.087280, -239.847733, 409.870544, 872.879395, 1022.795044, 873.666260, 542.853394, 166.554474, -167.279343, -421.786163, -574.097473, -598.089050, -483.041748, -254.029663, 32.983452, 313.140839, 530.974426, 646.964294, 634.547302, 472.122253, 147.337311, -307.988281, -777.549500, -1076.356812, -1041.862305, -639.906006, -3.258039, 627.224243, 1019.997986, 1058.309814, 778.791321, 328.092133, -128.916855, -480.979950, -678.768494, -706.788513, -571.692749, -312.830627, -2.018586, 281.551117, 482.149872, 581.096680, 587.120911, 511.118378, 341.525757, 48.834965, -364.046387, -804.371216, -1096.521729, -1071.784668, -678.150513, -29.260046, 641.286011, 1092.707397, 1190.510742, 955.440552, 523.230896, 51.563610, -351.070892, -631.735718, -764.643005, -739.103333, -569.061035, -297.871368, 11.910533, 296.090942, 506.303009, 618.688354, 623.469482, 502.190247, 226.953461, -194.704132, -666.769897, -1012.726929, -1059.489136, -739.174011, -139.794724, 526.005249, 1020.000305, 1191.244385, 1033.939941, 656.489502, 196.668289, -241.918991, -593.876038, -809.455444, -851.523987, -712.006409, -423.492371, -57.178764, 293.529572, 544.007385, 647.607971, 597.114014, 399.759949, 65.684921, -361.933929, -770.435852, -996.945129, -908.601013, -485.731812, 148.905838, 774.358765, 1172.452148, 1231.997437, 988.021790, 570.403076, 111.174576, -309.435486, -650.265259, -874.695374, -943.078857, -830.789673, -549.200439, -158.472488, 240.523285, 544.365601, 690.945496, 667.982178, 484.439728, 152.925064, -283.187164, -713.474548, -976.514343, -933.490662, -548.126709, 75.959641, 725.113892, 1171.680664, 1287.049683, 1090.618042, 700.101929, 238.092880, -219.184372, -626.005005, -932.521790, -1078.344971, -1013.246338, -727.736023, -281.502930, 197.579910, 565.700439, 733.216309, 689.774414, 472.586243, 131.442688, -266.758728, -619.505310, -804.915894, -732.608337, -391.217773, 131.661041, 668.325439, 1038.440430, 1137.567383, 977.325439, 643.162781, 220.841675, -232.770157, -664.235962, -996.922363, -1141.615723, -1032.854126, -669.180115, -141.638718, 381.070862, 728.032043, 812.889648, 657.162109, 342.352661, -43.942142, -418.562012, -691.860046, -778.799805, -631.565979, -266.258209, 227.356430, 701.222412, 1005.882080, 1066.377930, 909.265564, 612.325073, 235.768097, -191.485443, -631.678955, -1005.314697, -1202.858398, -1128.763794, -757.347168, -178.216354, 415.305908, 817.885559, 921.166382, 747.472229, 397.126923, -18.184418, -400.399261, -664.037537, -744.386292, -613.781189, -291.509766, 148.978867, 583.400879, 879.384460, 965.310730, 856.686523, 610.298706, 266.010010, -155.023590, -606.641541, -991.950623, -1185.763184, -1086.573486, -676.556458, -65.885094, 528.209900, 888.133118, 914.903137, 658.798706, 254.000549, -162.450150, -487.870148, -658.781006, -651.767273, -479.452698, -179.487640, 186.367355, 528.447144, 756.052856, 828.610535, 768.149353, 609.959229, 354.811157, -14.593460, -474.748230, -928.058533, -1224.218506, -1219.444092, -854.566162, -221.030792, 450.380310, 906.419739, 1011.121704, 793.001221, 385.805939, -56.588966, -410.206421, -600.565186, -608.571594, -457.952850, -192.008926, 131.698288, 433.674896, 634.063843, 700.223022, 656.146729, 531.724609, 317.760437, -12.809819, -443.454834, -879.437256, -1166.957764, -1152.953247, -770.552979, -114.103073, 571.186584, 1014.932007, 1071.716309, 773.711975, 272.835236, -246.651764, -628.053955, -777.697693, -682.358643, -396.556335, -9.394369, 376.529358, 656.513000, 759.677490, 694.086609, 535.226624, 350.417694, 140.910538, -135.560410, -493.793671, -872.286865, -1136.793091, -1131.998169, -772.994141, -134.684555, 548.764343, 1009.803589, 1101.822266, 853.228760, 408.550842, -60.423874, -415.769226, -585.908691, -571.281860, -416.630249, -174.072342, 103.170929, 347.553772, 494.936310, 528.093872, 479.491974, 377.637299, 206.975693, -66.296318, -435.151184, -818.725769, -1074.422485, -1050.078491, -672.039185, -28.004711, 642.241211, 1077.209717, 1142.943848, 876.922974, 423.860992, -50.863037, -417.910156, -612.580750, -635.311218, -520.143677, -301.678589, -19.688280, 258.555725, 455.156616, 531.574158, 501.479584, 387.296021, 184.982346, -116.019577, -487.734924, -841.844604, -1043.083374, -956.465759, -529.459473, 132.432846, 783.468384, 1171.966187, 1183.845703, 875.067993, 399.321716, -79.740265, -442.518738, -636.903320, -670.983459, -576.109375, -377.047791, -105.663452, 171.118942, 369.859772, 445.910583, 411.786255, 297.795013, 115.376068, -133.395035, -424.191345, -692.180847, -834.436401, -740.614075, -363.442932, 209.409515, 767.980042, 1099.329102, 1111.631470, 854.520813, 450.009674, 20.063293, -349.269409, -616.498230, -769.530457, -793.481812, -660.920105, -372.150116, 0.077071, 332.922424, 530.591064, 569.324524, 473.895905, 276.868469, 7.107396, -300.741333, -593.284546, -785.941223, -773.022827, -488.250763, 16.941895, 567.172424, 961.763489, 1089.747314, 959.195190, 648.523132, 251.607071, -152.048965, -508.109070, -776.329041, -905.309570, -835.379883, -552.295471, -137.426102, 259.496704, 509.432800, 564.496704, 448.187866, 217.146835, -64.654167, -339.211395, -555.973999, -657.235718, -574.706177, -272.954987, 188.000320, 652.827820, 958.781494, 1028.397217, 882.024170, 587.981689, 217.312500, -174.307831, -546.476379, -855.181824, -1028.830566, -983.051697, -688.163818, -225.378128, 242.500031, 566.114563, 678.680420, 595.164612, 376.183472, 93.846268, -192.581741, -440.042511, -598.278870, -596.081909, -380.553345, 16.457369, 466.137024, 813.472046, 960.457947, 887.852051, 628.399109, 241.260941, -201.639023, -624.697083, -945.996460, -1072.282593, -928.361389, -523.474976, 12.402433, 483.274445, 736.224854, 729.222717, 519.442383, 211.024033, -97.108887, -347.048370, -522.209717, -609.154907, -567.570496, -357.771332, -1.365258, 402.383270, 731.515930, 906.684631, 905.609070, 740.140320, 437.265442, 32.645508, -425.740631, -858.412537, -1141.060059, -1142.895630, -815.514343, -254.918900, 334.665802, 749.985168, 880.619263, 732.802063, 400.119537, 8.480625, -340.276764, -590.274475, -706.939941, -651.528931, -403.682831, -9.147440, 416.598877, 747.875244, 911.865845, 899.358826, 736.270508, 455.271088, 81.943359, -357.374390, -801.326111, -1126.858154, -1185.737793, -901.657410, -345.696075, 284.904724, 767.809631, 955.911316, 823.118164, 454.097137, -7.399651, -425.543121, -710.156982, -807.550659, -685.662842, -355.047180, 99.617210, 536.911194, 830.312500, 929.927490, 862.217224, 684.542175, 438.466949, 126.962883, -267.373108, -722.452332, -1126.115479, -1304.256958, -1127.624268, -611.782288, 73.785019, 689.399841, 1036.478027, 1034.282593, 735.224121, 278.123749, -188.407257, -554.988037, -749.778137, -726.534363, -482.914398, -87.599243, 333.361542, 655.133362, 808.506287, 790.158997, 636.430237, 386.950012, 59.064651, -342.242920, -773.755859, -1114.078491, -1199.634277, -928.588562, -347.548340, 352.589539, 926.310547, 1185.028564, 1070.648315, 663.105652, 123.478577, -388.154358, -760.144409, -924.819519, -846.875732, -540.937683, -93.010323, 359.285278, 686.880066, 823.600037, 777.609741, 602.848511, 353.563782, 50.119846, -310.526642, -696.913452, -997.930664, -1057.742554, -778.421753, -205.642838, 471.939362, 1007.400085, 1208.564331, 1018.662109, 527.763977, -86.718628, -646.538147, -1023.920532, -1143.522827, -978.276550, -567.073364, -25.908539, 484.229340, 823.750183, 930.947571, 834.925537, 623.118164, 382.193146, 146.975189, -98.770203, -363.817169, -595.321655, -695.577759, -598.472229, -332.464539, -15.038727, 216.302032, 286.267975, 219.930939, 109.030083, 32.211239, 4.282624, ])
ecg_clean = np.array([-8419.287109, -11295.071289, -12972.508789, -13625.854492, -13674.680664, -13478.679688, -13263.256836, -13140.885742, -13139.352539, -13249.303711, -13440.847656, -13603.796875, -13518.873047, -13000.458008, -12114.698242, -11184.899414, -10525.796875, -10217.981445, -10149.427734, -10177.799805, -10212.553711, -10221.736328, -10214.294922, -10179.371094, -10018.495117, -9590.146484, -8878.566406, -8088.625488, -7501.739746, -7244.872559, -7243.467773, -7350.206543, -7452.871094, -7503.522949, -7516.850098, -7521.640137, -7462.785156, -7174.493652, -6527.564453, -5624.697266, -4783.520020, -4282.278320, -4160.353516, -4267.216309, -4421.673828, -4508.630859, -4509.908691, -4481.103027, -4453.487793, -4341.477539, -3994.400635, -3375.223877, -2656.232178, -2091.834717, -1817.217896, -1799.755127, -1927.271729, -2088.678223, -2220.283203, -2327.942139, -2431.933105, -2458.726807, -2233.109375, -1643.380859, -817.914124, -83.080795, 285.341309, 249.030289, -30.462946, -340.337860, -539.409851, -625.990967, -705.427429, -843.291321, -947.803467, -835.387024, -422.504639, 168.853287, 703.122375, 1000.315613, 1013.710327, 810.510986, 516.153809, 228.267349, -41.865681, -304.210846, -467.672058, -349.442627, 149.590485, 889.615601, 1540.776489, 1808.025391, 1621.106689, 1143.586914, 645.621765, 333.716461, 221.682602, 161.782547, 37.485695, -88.845718, -36.447178, 311.513855, 897.891235, 1533.154541, 2016.510254, 2236.961182, 2217.492920, 2078.259766, 1918.784912, 1742.389526, 1539.806641, 1418.912109, 1574.300049, 2106.594727, 2890.097412, 3619.916016, 3997.181885, 3906.860352, 3471.286621, 2961.346191, 2609.883789, 2450.524658, 2347.374268, 2193.793457, 2042.252075, 2035.609131, 2260.966064, 2675.363037, 3127.841553, 3440.650635, 3511.183350, 3377.257324, 3168.429932, 2961.496582, 2717.987549, 2409.428711, 2157.515381, 2177.608887, 2586.003418, 3277.543701, 3961.825928, 4320.042480, 4192.212402, 3678.582520, 3070.730713, 2633.291016, 2412.679932, 2273.628174, 2108.147705, 1952.144897, 1915.192505, 2069.008057, 2394.942627, 2775.133301, 3039.640625, 3082.604492, 2951.215576, 2781.489502, 2630.160400, 2426.538574, 2127.035889, 1854.555420, 1825.886353, 2167.962402, 2812.081299, 3507.155029, 3933.175537, 3889.445557, 3439.389893, 2863.225342, 2425.338867, 2177.411621, 2006.093872, 1832.138428, 1696.584961, 1686.888428, 1856.958008, 2190.517822, 2571.876953, 2822.015625, 2836.217773, 2683.677246, 2517.613770, 2385.757568, 2195.844727, 1888.419922, 1570.478271, 1439.523926, 1626.202148, 2111.282471, 2710.791504, 3133.891846, 3156.383789, 2798.911133, 2305.639404, 1912.672607, 1657.388794, 1436.980957, 1195.829224, 990.148499, 919.416199, 1064.972412, 1436.624878, 1902.246948, 2227.227295, 2267.242188, 2098.693848, 1903.027832, 1747.592163, 1551.660400, 1261.440186, 971.195496, 850.073242, 1015.114014, 1466.375244, 2049.443359, 2482.697266, 2532.471680, 2208.837158, 1743.958008, 1355.329712, 1070.667969, 801.837585, 516.727844, 277.882446, 177.178940, 298.330017, 665.306641, 1148.183105, 1496.037109, 1552.243774, 1396.242432, 1212.894531, 1065.569946, 872.486450, 581.027771, 273.527069, 99.534012, 180.624390, 556.149658, 1110.418457, 1564.897949, 1663.539917, 1395.843018, 976.692810, 603.234863, 295.809448, -13.715532, -328.259338, -573.165894, -659.025391, -502.391296, -81.635063, 452.732880, 820.824768, 859.238525, 668.674255, 458.991364, 308.125305, 142.912170, -92.860001, -347.313477, -514.483704, -487.472168, -191.912155, 312.878632, 782.687805, 960.282227, 809.974976, 505.416138, 197.072235, -119.644104, -499.188049, -910.099426, -1247.328979, -1394.469604, -1238.329712, -744.491760, -92.188416, 383.847382, 483.143219, 304.931549, 76.768303, -98.780327, -264.933533, -458.970337, -643.069275, -748.714111, -692.305176, -389.859070, 123.577339, 619.862183, 847.467529, 768.469421, 539.076721, 280.723389, -27.687174, -432.378082, -886.298035, -1276.040894, -1472.702271, -1337.333740, -818.135925, -112.753105, 400.835846, 493.933319, 269.426910, -26.211182, -270.705017, -491.127350, -726.419739, -969.326599, -1185.553711, -1282.384399, -1112.878296, -643.852539, -86.483482, 269.684235, 331.735992, 211.433960, 6.108595, -299.107239, -719.138123, -1180.236572, -1565.337769, -1749.661255, -1588.166992, -1023.407166, -267.844757, 272.847809, 356.054321, 91.429131, -259.261597, -552.264771, -787.149902, -990.541016, -1178.733032, -1359.637817, -1461.485229, -1322.940186, -881.554260, -325.385681, 68.412018, 204.752274, 171.686981, 32.661671, -242.790253, -657.043823, -1114.410522, -1481.973389, -1624.574585, -1397.477783, -766.372559, 19.668394, 536.423645, 555.228760, 211.866913, -215.446823, -571.904480, -842.704590, -1048.936279, -1223.428833, -1399.610962, -1516.455688, -1404.678711, -988.175415, -444.026276, -41.614582, 124.374969, 129.271851, 19.391382, -239.798386, -643.523315, -1097.112427, -1478.612549, -1651.966919, -1449.924927, -813.657837, 11.698052, 585.027039, 652.559753, 324.985992, -134.550903, -560.008606, -900.845459, -1149.436157, -1341.079102, -1527.483521, -1653.216797, -1540.783569, -1111.461670, -551.466064, -137.951202, 36.204765, 51.524628, -40.415707, -267.476196, -628.795044, -1058.086426, -1469.359985, -1731.898926, -1640.217896, -1079.964966, -257.660431, 390.601471, 582.461914, 378.759247, -2.519412, -407.872894, -763.990906, -1032.221558, -1230.890015, -1404.373413, -1492.042847, -1323.174438, -843.867676, -265.332581, 131.219345, 266.687256, 237.320724, 110.626602, -120.600868, -443.553436, -806.897400, -1157.497803, -1387.494141, -1293.050537, -749.748047, 50.482288, 687.959045, 887.382202, 696.560242, 311.073029, -122.488457, -517.222351, -823.203796, -1064.823120, -1296.218628, -1452.996216, -1347.821655, -906.282898, -324.272278, 115.791130, 312.499023, 333.676636, 237.584641, 32.809895, -250.581055, -563.173950, -863.076294, -1046.010864, -912.030151, -355.098633, 414.034363, 982.059998, 1101.428711, 841.348938, 402.048950, -66.816521, -469.188477, -751.382080, -942.680542, -1099.296021, -1160.413818, -965.949341, -489.922638, 41.302917, 361.044556, 413.910797, 312.796936, 148.380234, -55.541332, -286.731750, -550.921204, -866.883240, -1152.724609, -1176.865479, -764.464966, -53.828854, 577.840149, 857.152893, 780.428162, 476.848785, 68.012794, -336.391174, -657.825317, -905.770752, -1115.150513, -1203.650024, -1004.661377, -502.839142, 62.399788, 415.728363, 491.962860, 397.106750, 233.893219, 55.690281, -107.302460, -275.062164, -497.988251, -720.156616, -728.713379, -359.846222, 263.367371, 809.554138, 1048.630371, 985.308105, 729.181274, 379.483490, 24.636124, -287.759674, -598.076355, -944.502197, -1210.968750, -1176.145020, -769.272095, -195.445816, 258.037842, 466.193329, 468.195313, 341.555054, 161.312775, -10.643161, -180.766235, -397.667511, -603.773376, -590.999268, -208.556686, 415.277496, 958.282166, 1198.374756, 1137.049194, 879.998352, 531.286804, 182.749756, -127.826385, -453.261200, -829.250488, -1126.337891, -1112.534302, -707.650818, -107.707138, 391.299316, 631.987122, 627.810791, 469.036011, 269.517334, 112.582817, -24.872261, -226.771149, -465.322845, -548.184570, -312.661560, 167.700836, 642.042480, 915.946777, 953.600891, 802.440369, 534.751953, 236.131195, -60.284557, -412.126251, -846.056213, -1211.484131, -1255.459351, -877.048523, -252.502090, 319.930084, 645.320557, 692.445129, 541.432190, 332.823029, 178.953873, 65.944977, -93.312141, -281.124084, -329.856628, -105.572266, 317.938019, 724.844421, 956.062866, 984.301025, 850.081482, 620.060303, 368.960266, 108.359459, -231.748917, -663.675476, -1013.877563, -1027.834473, -622.671875, 11.206614, 570.937012, 857.108643, 839.750732, 619.169495, 364.231354, 196.150909, 84.684807, -78.492294, -289.312744, -389.369232, -241.119446, 113.346214, 500.813477, 774.687378, 882.517212, 836.044250, 689.893066, 506.447296, 271.019623, -106.973145, -631.475586, -1097.506714, -1213.062744, -856.081482, -186.907471, 482.846680, 897.943909, 966.138794, 764.834290, 479.411926, 257.913849, 94.928734, -91.036613, -279.197876, -326.652374, -135.564468, 225.155212, 586.141479, 818.553101, 886.737610, 820.596558, 687.809082, 539.446960, 327.807617, -59.438484, -616.744324, -1116.720215, -1254.004883, -898.713562, -205.451492, 501.940918, 936.104431, 984.610413, 740.362183, 419.863007, 183.507431, 14.918512, -183.458572, -404.170563, -514.523865, -407.370453, -110.302589, 250.221832, 543.996887, 694.080017, 696.991394, 617.943176, 515.655701, 343.182129, -5.760604, -506.793030, -923.188538, -969.635315, -549.747620, 162.607697, 840.618835, 1199.476929, 1138.958740, 778.196472, 358.095551, 48.402718, -159.414383, -341.501556, -473.555817, -442.938812, -198.122116, 178.647476, 535.509827, 748.685608, 775.363220, 665.360413, 528.343018, 427.326630, 283.520386, -40.972332, -532.267700, -954.527161, -1021.211182, -620.058777, 102.300179, 825.397278, 1236.529541, 1204.629272, 843.597961, 402.849762, 53.356304, -215.316483, -474.261780, -695.578674, -769.085327, -628.359802, -307.285400, 87.727745, 423.051910, 597.726746, 612.139648, 564.189392, 523.118164, 415.483246, 110.640930, -371.950745, -806.794617, -924.338135, -601.433899, 61.127823, 780.392822, 1236.639404, 1265.501953, 955.115784, 539.505737, 176.922913, -143.555634, -474.918701, -769.424622, -908.976807, -816.991089, -503.415100, -62.151421, 346.112183, 573.167603, 595.796265, 522.045532, 442.912506, 307.756989, 14.878622, -392.812653, -698.622620, -676.721008, -252.428436, 445.308594, 1125.404419, 1479.099121, 1379.778564, 965.905701, 496.141510, 112.761551, -224.450592, -583.470642, -920.229736, -1116.802612, -1081.196533, -789.183228, -314.367218, 160.036957, 443.192261, 493.887787, 432.917084, 366.959290, 249.512466, -22.998783, -416.112000, -730.873047, -748.823059, -367.420197, 329.266205, 1060.177246, 1480.140137, 1426.220215, 1032.625244, 566.436462, 168.893112, -203.082947, -614.014404, -1019.869812, -1305.307495, -1358.521118, -1106.853149, -590.718628, -19.792263, 349.743713, 432.517609, 350.960907, 241.995346, 101.279373, -135.097443, -426.480164, -623.435669, -584.544739, -246.982544, 337.176544, 956.958618, 1318.681152, 1272.241821, 935.105591, 537.023987, 179.449860, -193.716995, -626.780457, -1047.378662, -1323.326782, -1334.039307, -1007.146667, -408.473480, 205.024246, 545.732849, 541.121460, 354.263947, 159.275040, -22.222488, -238.290985, -455.610077, -562.373291, -461.564056, -109.330093, 451.257355, 1025.062378, 1333.609741, 1249.550049, 911.847168, 546.979187, 229.096237, -122.103905, -559.148804, -1012.198730, -1344.766357, -1408.061890, -1086.428833, -431.302216, 262.960266, 654.870789, 648.928101, 420.100677, 167.281754, -60.059315, -286.975342, -483.468048, -573.924011, -497.640106, -208.424667, 287.308136, 826.410950, 1137.386963, 1088.031616, 809.420471, 508.828552, 235.565765, -98.148880, -530.512207, -975.989319, -1292.854126, -1330.092773, -971.326416, -281.163757, 418.876709, 770.727844, 691.214233, 383.496460, 71.152252, -175.876495, -369.198151, -491.636810, -511.484467, -413.009949, -162.808411, 253.250549, 705.218567, 953.684021, 891.625000, 655.946411, 431.156097, 230.345047, -58.883694, -485.189545, -970.573120, -1369.435547, -1495.855591, -1178.791992, -452.860809, 339.727814, 793.122314, 786.948792, 508.503113, 183.495590, -96.148918, -311.413147, -435.625397, -459.253479, -391.579895, -196.608551, 163.189484, 575.303894, 803.978943, 742.774658, 528.369324, 338.287354, 177.596832, -66.259041, -442.964142, -887.001282, -1263.367188, -1376.600708, -1037.172119, -280.122437, 530.237793, 970.416931, 921.985352, 581.161743, 181.682144, -164.833649, -407.170349, -498.233337, -435.207367, -251.273392, 56.887791, 483.051239, 875.727112, 1000.839172, 803.124451, 480.284760, 238.953415, 81.505608, -119.319283, -437.681427, -843.391907, -1224.990601, -1374.748657, -1067.707153, -317.268280, 505.342163, 960.578857, 923.690979, 591.322754, 199.333679, -134.376022, -358.561218, -450.770142, -446.529388, -389.419739, -235.341675, 77.090851, 445.704773, 641.847839, 575.779541, 391.437622, 250.327087, 143.858047, -31.759544, -323.101593, -693.273804, -1037.207031, -1150.663696, -813.847168, -54.613766, 745.894592, 1159.836792, 1085.168823, 726.187439, 309.219086, -53.901974, -309.769989, -439.852112, -488.033539, -491.031189, -380.420929, -75.084389, 322.651398, 569.434387, 555.166260, 401.825195, 258.573120, 129.787766, -56.194946, -325.019745, -645.965454, -930.110046, -982.658813, -594.678955, 185.753418, 963.371826, 1320.636108, 1182.230713, 771.400879, 318.784363, -63.437931, -325.550751, -464.465240, -539.726685, -582.991760, -504.188263, -208.254227, 200.247116, 470.795624, 486.064514, 357.665283, 230.850372, 127.291008, 2.055152, -168.250137, -385.324493, -599.156982, -634.622620, -284.650085, 414.007935, 1095.619385, 1382.836182, 1224.453857, 834.415833, 413.194855, 44.701786, -242.552322, -461.937500, -670.114258, -859.010986, -875.116394, -576.480530, -68.579720, 350.233093, 496.106537, 432.535187, 301.718262, 166.193115, 29.428032, -121.745781, -324.041840, -568.736145, -689.616394, -449.959503, 165.319122, 837.101257, 1198.403564, 1160.763672, 878.307373, 511.621429, 142.864426, -184.456726, -476.651337, -784.062988, -1074.813843, -1161.654907, -882.248413, -342.351807, 144.702026, 366.537628, 350.959991, 223.298920, 69.633324, -60.428570, -154.102142, -259.468475, -397.522888, -433.751404, -163.542862, 411.134796, 993.708923, 1268.773560, 1183.843872, 890.316895, 527.804321, 162.921219, -173.445084, -501.522308, -871.023987, -1225.146729, -1347.310059, -1064.307373, -486.364044, 63.956055, 355.789215, 388.686951, 271.889282, 105.603615, -33.418739, -125.172165, -234.989899, -401.865387, -494.939575, -299.684265, 208.545731, 773.704224, 1104.799072, 1126.830200, 935.295044, 627.534119, 267.058563, -93.994217, -449.445892, -818.141663, -1115.365356, -1128.334961, -731.237061, -90.789894, 447.351471, 664.504211, 584.648071, 346.262085, 85.650787, -93.554092, -174.896362, -251.252670, -388.513702, -473.652618, -304.239594, 149.382584, 663.024536, 979.701111, 1026.548340, 875.853882, 609.829834, 290.459991, -43.740376, -419.126007, -875.695862, -1311.811279, -1466.449585, -1155.425903, -497.647308, 167.987305, 567.029358, 634.157837, 450.363434, 160.511749, -84.561333, -228.210464, -343.896942, -489.145844, -553.278625, -350.348358, 132.815552, 670.338562, 1008.185852, 1066.092041, 910.082275, 636.707703, 331.243683, 31.971535, -316.177094, -779.184875, -1256.068359, -1469.554077, -1212.668457, -574.679443, 126.059204, 598.247192, 726.877136, 553.259460, 222.432724, -87.806824, -292.781647, -442.039246, -572.933044, -574.456848, -291.165863, 249.588928, 801.620056, 1114.101074, 1119.578979, 905.446350, 601.203125, 316.023499, 73.401825, -231.022430, -708.754944, -1272.029663, -1622.162964, -1498.661255, -918.257446, -155.738266, 465.816132, 745.852722, 659.459900, 344.665436, 6.723244, -245.786057, -450.017395, -637.844360, -703.717834, -500.333282, -36.810696, 488.185669, 851.584167, 955.606628, 830.832825, 579.907837, 323.195831, 102.810669, -173.098740, -599.946106, -1075.609619, -1312.113770, -1085.642090, -446.215027, 320.008362, 891.370178, 1074.452148, 864.981445, 432.181244, 1.369997, -318.860535, -567.752319, -769.566589, -817.325928, -581.328857, -90.940552, 449.408813, 814.850220, 899.349915, 735.825256, 453.245300, 199.772278, 17.893709, -203.970261, -573.629028, -991.193909, -1177.857788, -922.822571, -273.992432, 494.324188, 1058.230103, 1209.947266, 944.719421, 450.730255, -29.369543, -380.072144, -630.691650, -792.447632, -765.915466, -456.667389, 72.606918, 611.320251, 942.779175, 964.640991, 719.381592, 364.158905, 75.282272, -102.843353, -301.867950, -649.684998, -1060.486206, -1265.767700, -1047.613403, -421.913574, 363.084381, 970.311340, 1161.003052, 931.850464, 510.613281, 173.178391, 27.279436, ])

In [ ]:
x = np.arange(0, len(ppg1))
fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=ppg1_clean, name='PPG1 Clean'))
fig.add_trace(go.Scatter(x=x, y=ppg2_clean, name='PPG2 Clean'))
fig.add_trace(go.Scatter(x=x, y=ecg_clean, name='ECG Clean'))
fig.add_trace(go.Scatter(x=x, y=qrs_clean, name='QRS Clean'))

fig.show()

In [ ]:
ecg_hrv = pk.hrv.compute_hrv_time(rr_intervals=qrs_rr_ints[qrs_rr_mask == 0], sample_rate=fs)
print(dataclasses.asdict(ecg_hrv))

In [ ]:
qrs_rr_ints[qrs_rr_mask == 0]

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ecg - ecg.mean(), name='ECG'))  
fig.add_trace(go.Scatter(x=ts, y=ecg_clean, name='ECG Clean'))
fig.add_trace(go.Scatter(x=ts, y=qrs_clean, name='QRS Clean'))
fig.add_trace(go.Scatter(x=ts[qrs_peaks], y=ecg_clean[qrs_peaks], mode='markers', name='QRS Peaks'))
fig.show()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ppg1 - ppg1.mean(), name='PPG1'))  
fig.add_trace(go.Scatter(x=ts, y=ppg1_clean, name='PPG1 Clean'))
fig.add_trace(go.Scatter(x=ts[ppg1_peaks], y=ppg1_clean[ppg1_peaks], mode='markers', name='PPG1 Peaks'))
fig.show()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ppg2 - ppg2.mean(), name='PPG2'))  
fig.add_trace(go.Scatter(x=ts, y=ppg2_clean, name='PPG2 Clean'))
fig.add_trace(go.Scatter(x=ts, y=10*np.gradient(ppg2_clean), name='PPG2 Derivative'))

fig.add_trace(go.Scatter(x=ts[ppg2_peaks], y=ppg2_clean[ppg2_peaks], mode='markers', name='PPG2 Peaks'))

fig.show()

In [ ]:
max30101_spo2_coefs = [1.5958422, -34.6596622, 112.6898759]
MAX8614x_spo2_coefs = [-16.666666, 8.333333, 100]
spo2_coefs = max30101_spo2_coefs

win_len = int(5*fs)
ovp_len = int(0.5*fs)

for i in range(0, ppg1.shape[0] - win_len + 1, win_len - ovp_len):
    ppg1_win = ppg1[i:i+win_len]
    ppg2_win = ppg2[i:i+win_len]

    spo2_pk_t = pk.ppg.compute_spo2_in_time(
        ppg1=ppg1_win.copy(), 
        ppg2=ppg2_win.copy(), 
        coefs=spo2_coefs,
        sample_rate=fs
    )    

    spo2_pk_f = pk.ppg.compute_spo2_in_frequency(
        ppg1=ppg1_win.copy(), 
        ppg2=ppg2_win.copy(), 
        coefs=spo2_coefs,
        sample_rate=fs
    )

    ppg1_clean = pk.ppg.clean(data=ppg1_win, sample_rate=fs)
    ppg2_clean = pk.ppg.clean(data=ppg2_win, sample_rate=fs)

    ppg1_peaks = pk.ppg.find_peaks(ppg1_clean, sample_rate=fs)
    ppg1_peaks = pk.ppg.filter_peaks(ppg1_peaks, sample_rate=fs)

    ppg2_peaks = pk.ppg.find_peaks(ppg2_clean, sample_rate=fs)
    ppg2_peaks = pk.ppg.filter_peaks(ppg2_peaks, sample_rate=fs)

    hr = pk.ppg.compute_heart_rate(ppg2_clean, sample_rate=fs)
    print(f"SpO2: {spo2_pk_t/100:0.2%} | {spo2_pk_f/100:0.2%}")
    print(f"  HR: {hr:0.2f} bpm")
    # freqs, sp = pk.ppg.compute_fft(ppg1_clean, sample_rate=fs)

    # fig = go.Figure()
    # fig.add_trace(go.Scatter(x=fft_freqs[l_idx:r_idx], y=ppg1_ps, name='PPG1'))
    # fig.add_trace(go.Scatter(x=fft_freqs[l_idx:r_idx], y=ppg2_ps, name='PPG2'))
    # fig.show()

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=ts, y=ppg1_clean, name='PPG1'))
    fig.add_trace(go.Scatter(x=ts, y=ppg2_clean, name='PPG2'))
    fig.add_trace(go.Scatter(x=ts[ppg1_peaks], y=ppg1_clean[ppg1_peaks], mode="markers", name="PPG1 Peaks"))
    fig.add_trace(go.Scatter(x=ts[ppg2_peaks], y=ppg2_clean[ppg2_peaks], mode="markers", name="PPG2 Peaks"))
    fig.show()
    

In [ ]:
sample_rate = 1000
duration = 20
heart_rate = np.random.uniform(40, 120)
frequency_modulation = np.random.uniform(0.1, 0.4)
ibi_randomness = np.random.uniform(0.05, 0.2)

drift_amplitude = np.random.uniform(0.5, 2.0)
drift_frequency = max(0.05, (1 / duration) * 2)

powerline_amplitude = np.random.uniform(0.005, 0.01)   
powerline_frequency = np.random.uniform(50, 60)

motion_amplitude = np.random.uniform(0.5, 2.0)
motion_frequency = np.random.uniform(0.4, 0.6)

burst_frequency = np.random.uniform(80, 100)
burst_amplitude = np.random.uniform(0.0, 1.0)
burst_number = np.random.randint(0, 10)

num_noise_srcs = np.random.randint(1, 4)
noise_amplitude = [np.random.uniform(0.005, 0.025) for _ in range(num_noise_srcs)]
noise_frequency = [np.random.uniform(10, 40) for _ in range(num_noise_srcs)]

ppg_syn = pk.ppg.synthesize(
    duration=duration,
    sample_rate=sample_rate,
    heart_rate=heart_rate,
    frequency_modulation=frequency_modulation,
    ibi_randomness=ibi_randomness
)

ppg_syn_noise = ppg_syn.copy()

# Add baseline wander
ppg_syn_noise = pk.signal.add_baseline_wander(
    data=ppg_syn_noise,
    amplitude=drift_amplitude,
    frequency=drift_frequency,
    sample_rate=sample_rate,
)

# Add motion artifacts
ppg_syn_noise = pk.signal.add_motion_noise(
    data=ppg_syn_noise,
    amplitude=motion_amplitude,
    frequency=motion_frequency,
    sample_rate=sample_rate,
)

# Add high frequency bursts
ppg_syn_noise = pk.signal.add_burst_noise(
    data=ppg_syn_noise,
    amplitude=burst_amplitude,
    frequency=burst_frequency,
    burst_number=burst_number,
    sample_rate=sample_rate,
)

# Add powerline noise
ppg_syn_noise = pk.signal.add_powerline_noise(
    data=ppg_syn_noise,
    amplitude=powerline_amplitude,
    frequency=powerline_frequency,
    sample_rate=sample_rate
)

# Add additional noise sources
ppg_syn_noise = pk.signal.add_noise_sources(
    data=ppg_syn_noise,
    amplitudes=noise_amplitude,
    frequencies=noise_frequency,
    sample_rate=sample_rate
)

ppg_syn_clean = pk.ppg.clean(
    data=ppg_syn_noise, 
    sample_rate=sample_rate
)

ppg_peaks1 = pk.ppg.find_peaks(ppg_syn_clean, sample_rate=sample_rate)
ppg_peaks1 = pk.ppg.filter_peaks(ppg_peaks1, sample_rate=sample_rate)


In [ ]:
ts = np.arange(ppg_syn.size) / sample_rate
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ppg_syn, name='PPG base'))
fig.add_trace(go.Scatter(x=ts, y=ppg_syn_noise, name='PPG noise'))
fig.add_trace(go.Scatter(x=ts, y=ppg_syn_clean, name='PPG clean'))
fig.add_trace(go.Scatter(x=ts[ppg_peaks1], y=ppg_syn_clean[ppg_peaks1], mode="markers", name='Peaks1'))

# fig.add_trace(go.Scatter(x=ts[ppg_peaks_filt], y=1.2*ppg_syn_clean[ppg_peaks_filt], mode="markers", name='Peaks cleaned'))
fig.show()

In [ ]:
rsp_signal = pk.rsp.synthesize(
    duration=40,
    sample_rate=sample_rate,
    respiratory_rate=20
)

rsp_noise = rsp_signal.copy()

rsp_noise = pk.signal.add_baseline_wander(
    data=rsp_noise,
    amplitude=drift_amplitude,
    frequency=drift_frequency,
    sample_rate=sample_rate,
)

rsp_noise = pk.signal.add_motion_noise(
    data=rsp_noise,
    amplitude=motion_amplitude,
    frequency=motion_frequency,
    sample_rate=sample_rate,
)

rsp_noise = pk.signal.add_noise_sources(
    data=rsp_noise,
    amplitudes=noise_amplitude,
    frequencies=noise_frequency,
    sample_rate=sample_rate
)

rsp_clean = pk.rsp.clean(rsp_signal, sample_rate=sample_rate, lowcut=5/60, highcut=120/60)

In [ ]:
pk.rsp.compute_respiratory_rate(rsp_clean, sample_rate=sample_rate, method="fft")

In [ ]:
ts = np.arange(rsp_signal.size) / sample_rate
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=rsp_noise, name='RSP Signal'))
fig.add_trace(go.Scatter(x=ts, y=rsp_clean, name='RSP clean'))
# fig.add_trace(go.Scatter(x=ts[ppg_peaks1], y=ppg_syn_clean[ppg_peaks1], mode="markers", name='Peaks1'))
# fig.add_trace(go.Scatter(x=ts[ppg_peaks2], y=1.2*ppg_syn_clean[ppg_peaks2], mode="markers", name='Peaks2'))
fig.show()

In [59]:
sample_rate = 1000
duration = 20
heart_rate = np.random.uniform(40, 120)
frequency_modulation = np.random.uniform(0.1, 0.4)
hr_std_randomness = np.random.uniform(0.5, 1.5)

drift_amplitude = np.random.uniform(0.5, 2.0)
drift_frequency = max(0.05, (1 / duration) * 2)

powerline_amplitude = np.random.uniform(0.005, 0.01)   
powerline_frequency = np.random.uniform(50, 60)

motion_amplitude = np.random.uniform(0.5, 2.0)
motion_frequency = np.random.uniform(0.4, 0.6)

burst_frequency = np.random.uniform(80, 100)
burst_amplitude = np.random.uniform(0.0, 1.0)
burst_number = np.random.randint(0, 10)

num_noise_srcs = np.random.randint(1, 4)
noise_amplitude = [np.random.uniform(0.04, 0.2) for _ in range(num_noise_srcs)]
noise_frequency = [np.random.uniform(10, 40) for _ in range(num_noise_srcs)]

ecg_syns = pk.ecg.synthesize(
    duration=duration,
    sample_rate=sample_rate,
    heart_rate=heart_rate,
    heart_rate_std=hr_std_randomness,
    leads=12
)

ecg_syn = ecg_syns[9]

ecg_syn_noise = ecg_syn.copy()

ecg_syn_noise = (ecg_syn_noise - np.mean(ecg_syn_noise))/np.std(ecg_syn_noise)

ecg_syn_noise /= 100

# Add baseline wander
ecg_syn_noise = pk.signal.add_baseline_wander(
    data=ecg_syn_noise,
    amplitude=drift_amplitude,
    frequency=drift_frequency,
    sample_rate=sample_rate,
)

# Add motion artifacts
ppg_syn_noise = pk.signal.add_motion_noise(
    data=ecg_syn_noise,
    amplitude=motion_amplitude,
    frequency=motion_frequency,
    sample_rate=sample_rate,
)

# Add high frequency bursts
ecg_syn_noise = pk.signal.add_burst_noise(
    data=ecg_syn_noise,
    amplitude=burst_amplitude,
    frequency=burst_frequency,
    burst_number=burst_number,
    sample_rate=sample_rate,
)

# Add powerline noise
ecg_syn_noise = pk.signal.add_powerline_noise(
    data=ecg_syn_noise,
    amplitude=powerline_amplitude,
    frequency=powerline_frequency,
    sample_rate=sample_rate
)

# Add additional noise sources
ecg_syn_noise = pk.signal.add_noise_sources(
    data=ecg_syn_noise,
    amplitudes=noise_amplitude,
    frequencies=noise_frequency,
    sample_rate=sample_rate
)

ecg_syn_clean = pk.ecg.clean(
    data=ecg_syn_noise, 
    sample_rate=sample_rate
)

ecg_peaks = pk.ecg.find_peaks(ecg_syn_clean, sample_rate=sample_rate)
ecg_peaks = pk.ecg.filter_peaks(ecg_peaks, sample_rate=sample_rate)


In [60]:
ts = np.arange(ecg_syn.size) / sample_rate
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ecg_syn, name='ECG Lead'))
fig.add_trace(go.Scatter(x=ts, y=ecg_syn_noise, name='ECG noise'))
fig.add_trace(go.Scatter(x=ts, y=ecg_syn_clean, name='ECG clean'))
fig.add_trace(go.Scatter(x=ts[ecg_peaks], y=ecg_syn_clean[ecg_peaks], mode="markers", name='Peaks1'))
fig.show()

In [56]:
ecg_syns.T.shape

(20000, 12)

In [ ]:
ecg_win = ecg_clean[:20*fs]
ppg_win = ppg1_clean[:20*fs]

In [ ]:
ts = np.arange(ecg_win.size)
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=ecg_win, name='ECG'))  
fig.add_trace(go.Scatter(x=ts-70, y=100*np.abs(ppg_win), name='PPG'))
fig.add_trace(go.Scatter(x=ts[:-70], y=ecg_win[:-70]*np.abs(ppg_win[70:])))
fig.show()

In [ ]:
ppg_win

In [ ]:
def compute_ecg_fft(data, sample_rate, axis=-1):
    data_len = data.shape[axis]
    fft_len = int(2**np.ceil(np.log2(data_len)))
    fft_win = np.blackman(data_len)
    amp_corr = 1.93

    freqs = np.fft.fftfreq(fft_len, 1 / sample_rate)
    sp = amp_corr*np.fft.fft(fft_win*data, fft_len, axis=axis)/data_len
    return freqs, sp

In [ ]:
freqs, sp = pk.ppg.compute_fft(ppg1_clean, fs)

In [ ]:
freqs, sp = compute_ecg_fft(ecg_clean, sample_rate=fs)
freqs2, sp2 = compute_ecg_fft(ppg1_clean, sample_rate=fs)

In [ ]:
sp_len = len(freqs)//2
fig = go.Figure()
fig.add_trace(go.Scatter(x=freqs[:sp_len], y=np.abs(sp[:sp_len]), name='PPG PS'))
# fig.add_trace(go.Scatter(x=freqs[:sp_len], y=np.abs(sp2[:sp_len]), name='ECG'))
fig.show()

In [ ]:
sp_len = len(freqs)//2
fig = go.Figure()
fig.add_trace(go.Scatter(x=freqs[:sp_len], y=np.abs(sp[:sp_len]), name='PPG PS'))
# fig.add_trace(go.Scatter(x=freqs[:sp_len], y=np.abs(sp2[:sp_len]), name='ECG'))
fig.show()

In [ ]:
rr_ints = np.diff(ecg_peaks)

In [ ]:
rr_mu = np.nanmean(rr_ints)
rr_std = np.nanstd(rr_ints)

In [ ]:
rr_ints*1000/fs

In [ ]:
print(rr_mu-3*rr_std, rr_mu+3*rr_std)

In [ ]:
pk.signal.quotient_filter_mask(rr_ints, lowcut=0.8, highcut=1.2)

In [ ]:
x = np.array([1,9,-3,5])
win = np.ones((4,))/4

In [ ]:
qrs_width = int(0.1*fs)
qrs_idxs = [idx for idx in filt_qrs_peaks if idx-0.5*qrs_width>=0 and idx+0.5*qrs_width<len(ecg_clean)]
qrs_complexes = np.zeros((len(qrs_idxs), qrs_width))
for i, idx in enumerate(qrs_idxs):
    qrs_complexes[i] = ecg_clean[int(idx-0.5*qrs_width):int(idx+0.5*qrs_width)]
master_qrs = np.mean(qrs_complexes, axis=0)
ecg_conv = signal.convolve(ecg_clean, master_qrs, mode='same')/np.sum(master_qrs)

In [ ]:
fig = go.Figure()
# for i, idx in enumerate(qrs_idxs):
#     fig.add_trace(go.Scatter(x=np.arange(qrs_width), y=qrs_complexes[i], name=f'ECG {i}'))   
# fig.add_trace(go.Scatter(x=np.arange(qrs_width), y=master_qrs, name='Master ECG'))
fig.add_trace(go.Scatter(x=np.arange(ecg.size), y=ecg-ecg.mean(), name='ECG Raw'))
fig.add_trace(go.Scatter(x=np.arange(ecg_clean.size), y=ecg_clean, name='ECG Clean'))
fig.add_trace(go.Scatter(x=np.arange(ecg_conv.size), y=ecg_conv-ecg_clean, name='ECG Conv'))

fig.show()

In [ ]:
ecg_clean.shape